### LIBRARY IMPORT

In [2]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
# pd.set_option('display.max_rows', None)
from contextlib import contextmanager
import time  
from sklearn.neighbors import NearestNeighbors  
from sklearn.preprocessing import minmax_scale  
from typing import Dict, List, Optional, Tuple  
import seaborn as sns 
import gc
import traceback 

import matplotlib.pyplot as plt

from scipy.stats import kendalltau

import os
# os.environ["MODIN_ENGINE"] = "dask"  # Modin will use Dask
working_directory = 'D:\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'  ## 서로 다른 환경에서는 이곳을 수정해야 함.
# working_directory = 'C:\\Users\\user\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'

os.chdir(working_directory)
gc.collect()



23

### Drop Early morning period & CHECK NULL VALUE

In [101]:
# combined_result_df = pd.read_csv("./DB/professor_BTC_sum_both_10m.csv")
combined_result_df_raw = pd.read_csv("./output/BTC_sum_both_10m.csv")
print("# of rows of combined_Result_Df:", combined_result_df_raw.shape[0])

combined_result_df_raw['window_start'] = pd.to_datetime(combined_result_df_raw['window_start'])  # Convert to datetime

# Define the time range
start_time = pd.to_datetime('00:00:00').time()
end_time = pd.to_datetime('06:00:00').time()

# 10분간 return 추가
combined_result_df_raw['return'] = np.log(combined_result_df_raw['end_price'].shift(-10) / combined_result_df_raw['end_price'])

# Filter and drop rows (새벽시간 삭제하기)
filtered_df = combined_result_df_raw[~combined_result_df_raw['window_start'].apply(lambda x: start_time <= x.time() <= end_time)]
print("# of rows of filtered_df:", filtered_df.shape[0])

# Set the target variable:
target_var = 'dv5_realized_volatility_mean0'
target_var_3 = target_var[:3]
print("target_var_3:", target_var_3)

# 사용하지 않을 변수(column)들 미리 제거 (dropna 효과를 최소화하기 위해.)
remove_varlist0 = [
                  'window_start', 
                  'window_end',
                  'prices_30s_for_NN',
                  'window_end_150_ticker',
                  'window_end_300_ticker',
                  'window_end_450_ticker',
                  'window_end_150_orderbook',
                  'window_end_300_orderbook',
                  'window_end_450_orderbook',

                  'volume_power',
                  'volume_power_150',
                  'volume_power_300',
                  'volume_power_450',
                  
                  'end_price',
                  'realized_volatility_30s',

                #   'dv1_realized_volatility',
                  'dv2_lowest_return',
                  'dv3_highest_return',
                  'dv4_realized_volatility_30s',
                  'dv5_realized_volatility_mean0',

                  # 'prices_30s_for_NN_onlyprices',
                  ]
remove_varlist0.remove(target_var)

# 이 두 아래의 변수도 NN feature를 뽑을 때에는 활용해보자.
remove_varlist0.remove('dv2_lowest_return')
remove_varlist0.remove('dv3_highest_return')

main_feature_list = list(filtered_df.columns)

for i in range(len(remove_varlist0)):
    # print(remove_varlist0[i])
    main_feature_list.remove(remove_varlist0[i])

## 제거하기 전에, 30초 주가 데이터를 따로 저장.
# listed_time_series_df = filtered_df['only_prices_30s_for_NN'].copy()
# combined_result_df = combined_result_df.drop('prices_30s_for_NN_onlyprices', axis=1)

filtered_df = filtered_df[main_feature_list]

combined_result_df = filtered_df.dropna()
print("# of rows of filtered_df:", combined_result_df.shape[0])

# 평균이 아닌 이전 값으로 Null 채우기
# combined_result_df = combined_result_df.fillna(method='ffill') 

# Temporary take the first N rows
take_first_rows = 20000
combined_result_df = combined_result_df.head(take_first_rows)

print("combined_result_df.dtypes:", combined_result_df.dtypes)
print("combined_result_df.shape:", combined_result_df.shape)
combined_result_df.head(3)

gc.collect()

# of rows of combined_Result_Df: 102336
# of rows of filtered_df: 76766
target_var_3: dv5
# of rows of filtered_df: 76696
combined_result_df.dtypes: realized_volatility_mean0    float64
num_trades                     int64
lowest_return                float64
highest_return               float64
high_low_gap                 float64
                              ...   
tvpl_ep2                     float64
tvpl_ep5                     float64
tvpl_ep10                    float64
tvpl_ep15                    float64
return                       float64
Length: 92, dtype: object
combined_result_df.shape: (20000, 92)


0

In [102]:
import re
def extract_floats_from_series(df):
    def extract_floats(s):
        return [float(num) for num in re.findall(r"(-?\d+\.\d+)", s)]

    df['only_prices_30s_for_NN'] = df['prices_30s_for_NN_onlyprices'].apply(extract_floats)
    
    # 데이터 포인트가 20개가 아닌 행을 삭제
    mask = df['only_prices_30s_for_NN'].apply(len) == 20
    df = df[mask].reset_index(drop=True)
    
    return df

In [103]:
combined_result_df = extract_floats_from_series(combined_result_df)
print("combined_result_df.shape (After dropping windows without 20 prices):", combined_result_df.shape)
listed_time_series_df = combined_result_df['only_prices_30s_for_NN'].copy()
combined_result_df = combined_result_df.drop('prices_30s_for_NN_onlyprices', axis=1)
combined_result_df = combined_result_df.drop('only_prices_30s_for_NN', axis=1)

gc.collect()

combined_result_df.shape (After dropping windows without 20 prices): (18882, 93)


0

In [104]:
float64_features = combined_result_df.select_dtypes(include=['float64']).columns.tolist()
int64_features = combined_result_df.select_dtypes(include=['int64']).columns.tolist()

combined_result_df[float64_features] = combined_result_df[float64_features].astype('float32')
combined_result_df[int64_features] = combined_result_df[int64_features].astype('int32')

gc.collect()

0

In [105]:
print("combined_result_df.dtypes:", combined_result_df.dtypes)

combined_result_df.dtypes: realized_volatility_mean0    float32
num_trades                     int32
lowest_return                float32
highest_return               float32
high_low_gap                 float32
                              ...   
tvpl_ep2                     float32
tvpl_ep5                     float32
tvpl_ep10                    float32
tvpl_ep15                    float32
return                       float32
Length: 91, dtype: object


### Manipulating Features => Log transformation of some liquidity measures (Why?)

In [106]:
# combined_result_df['liq_last_1'] = np.log10(combined_result_df['liq_last_1'] + 0.00001)
# combined_result_df['liq_last_2'] = np.log10(combined_result_df['liq_last_2'] + 0.00001)
# combined_result_df['liq_last_5'] = np.log10(combined_result_df['liq_last_5'] + 0.00001)
# combined_result_df['liq_last_10'] = np.log10(combined_result_df['liq_last_10'] + 0.00001)
# combined_result_df['liq_last_15'] = np.log10(combined_result_df['liq_last_15'] + 0.00001)
# combined_result_df['trade_vol'] = np.log10(combined_result_df['trade_vol'] + 0.00001)
# combined_result_df['num_trades'] = np.log10(combined_result_df['num_trades'] + 0.00001)

### NUMERIC FEATURES & CALCULATE CORR 

In [107]:
## 이웃을 찾는 기준이 되는 변수들.

feature_list_for_finding_NN = []
feature_list_for_finding_NN.append('realized_volatility_mean0')
feature_list_for_finding_NN.append('bidask_spread_0')
feature_list_for_finding_NN.append('bidask_spread_1')
feature_list_for_finding_NN.append('highest_return')
feature_list_for_finding_NN.append('lowest_return')
feature_list_for_finding_NN.append('num_trades')
feature_list_for_finding_NN.append('high_low_gap')
feature_list_for_finding_NN.append('BB_width_w10')
feature_list_for_finding_NN.append('BB_width_w20')
feature_list_for_finding_NN.append('BB_width_w40')
feature_list_for_finding_NN.append('liq_last_1')
feature_list_for_finding_NN.append('liq_last_2')
feature_list_for_finding_NN.append('liq_last_5')
feature_list_for_finding_NN.append('ep_liq_1')
feature_list_for_finding_NN.append('ep_liq_2')
feature_list_for_finding_NN.append('ep_liq_5')
feature_list_for_finding_NN.append('tvpl1')
feature_list_for_finding_NN.append('tvpl2')
feature_list_for_finding_NN.append('tvpl5')
feature_list_for_finding_NN.append('tvpl_ep1')
feature_list_for_finding_NN.append('tvpl_ep2')
feature_list_for_finding_NN.append('tvpl_ep5')
feature_list_for_finding_NN.append('trade_vol')
feature_list_for_finding_NN.append('trade.tau')
feature_list_for_finding_NN.append('return')

# feature_list_for_finding_NN.append('volume_power')


In [108]:
main_feature_list = list(combined_result_df.columns)
feature_list_for_finding_NN.append(target_var)


# feature_list_for_corr = list(combined_result_df.columns)

# remove_varlist = [
#                   'time_id'
#                   ]

# for i in range(len(remove_varlist)):
#     # print(remove_varlist[i])
#     feature_list_for_corr.remove(remove_varlist[i])


gc.collect()

23

In [109]:
data = combined_result_df
correlation_matrix = data[feature_list_for_finding_NN].corr(method=lambda x, y: kendalltau(x, y).correlation)
feature_list_for_finding_NN.remove(target_var)

correlation_matrix_series = correlation_matrix[target_var].copy() # .sort_values(ascending=False)
correlation_matrix_series.sort_values(ascending=False, inplace=True)

gc.collect()

23

In [110]:
# correlation_matrix_series

In [111]:
combined_result_df_mfl = combined_result_df

In [112]:
combined_result_df_mfl.reset_index(drop=True, inplace=True)

In [113]:
combined_result_df_mfl.shape

(18882, 91)

In [114]:
import re
from joblib import Parallel, delayed
from numba import jit

# Numba를 사용하여 최적화된 Hausdorff 거리 계산 함수
@jit(nopython=True)
def compute_hausdorff_modified_numba(x, y):
    min_distances = np.abs(np.subtract(x, y))
    return np.max(min_distances)

# 주어진 시계열 대상과 다른 모든 시계열 간의 거리를 계산하는 함수
def compute_distances(target_series, series_list):
    return [compute_hausdorff_modified_numba(target_series, s) for s in series_list]

# 병렬 처리를 사용하여 특정 시계열과 가장 유사한 시계열의 인덱스를 찾는 함수
def parallel_similarity(df, idx, num_similar, window_size ):
    if window_size > idx :
        return np.array([0] * num_similar)
    
    target_series = np.array(df.iloc[idx])
    
    other_series = []
    
    for series in df.iloc[idx-window_size:idx] :
        other_series.append(np.array(series))
            
    distances = compute_distances(target_series, other_series)
    similar_indices = list(np.argsort(distances)[:num_similar])
    
    similar_indices = [idx - window_size + x for x in similar_indices]
    
    return similar_indices

# 병렬 처리를 사용하여 모든 시계열 간의 유사도를 계산하는 함수
def compute_similarity_parallel(df, num_similar=10, window_size = 10000):
    # 빈 2D 배열 생성
    results = np.array([]).reshape(0, num_similar)  # 2D 배열, 0행 2열
    
    for idx in range(len(df)):
        # if (idx + 1) % (len(df) // 10) == 0:
        #     print(f"Processed {idx + 1} rows ({((idx + 1) / len(df)) * 100:.1f}%)")
        result = parallel_similarity(df, idx, num_similar, window_size)
        results = np.append(results, [result], axis=0)
        
    return results

### BUILD NEIGHBORS

In [116]:
N_NEIGHBORS_MAX = 10        
WINDOW_SIZE = 10000

class Neighbors:
    def __init__(self, 
                 name: str, 
                 pivot: pd.DataFrame, 
                 p: float, 
                 metric: str = 'minkowski', 
                 metric_params: object = None, 
                 exclude_self: bool = True,
                 haus_metric = False,
                 ):
        self.name = name
        self.exclude_self = exclude_self
        self.p = p
        self.metric = metric
        self.neighbors = np.empty((0, N_NEIGHBORS_MAX), dtype=int)  # 빈 2D 배열로 초기화

        nn = NearestNeighbors(
            n_neighbors=N_NEIGHBORS_MAX, 
            p=p, 
            metric=metric, 
            metric_params=metric_params
        )
        
        # nn.fit(pivot)
        # _, self.neighbors = nn.kneighbors(pivot, return_distance=True)

        # 이웃을 찾을 이전 window 벙뮈
        window_size = WINDOW_SIZE

        if haus_metric == True : 
            # print("Checkpoint-haus_metric-BEGIN")

            self.neighbors = compute_similarity_parallel(listed_time_series_df, num_similar=N_NEIGHBORS_MAX, window_size = WINDOW_SIZE)
            self.neighbors = self.neighbors.astype(int)
            # print("Checkpoint-haus_metric-END")

        else:
            col_names = pivot.columns
            index_name = pivot.index.name
            
            for t in range(len(pivot)) :
                if t % 1000 == 0:
                    print("name: {}, iteration: {}".format(self.name, t))
                # window size 까지의 데이터는 random NN 설정
                # 1 ~ window 범위의 데이터는 추후 버려야 함
                if t < window_size :
                    update_array = np.random.permutation(np.arange(1, N_NEIGHBORS_MAX+1))
                    self.neighbors = np.append(self.neighbors, [update_array], axis = 0)
                    
                else :
                    # print("Checkpoint#1")

                    # pvdf = pd.DataFrame(pivot.iloc[t-window_size:t])
                    pvdf = pivot.iloc[t-window_size:t].values
                    # print("Checkpoint#1-1-0, pvdf.head(1):", pvdf.head(1))

                    # print("Checkpoint#1-1-1, list(col_names):", list(col_names))
                    # print("Checkpoint#1-1-2, type([list(col_names)]):", type([list(col_names)]))

                    # # col_names = list(col_names)
                    # # pvdf.columns = col_names
                    # print("Checkpoint#1-2")
                    # print("Checkpoint#1-2-1, //after// pvdf.columns:", pvdf.columns)

                    # pvdf.columns = list(col_names)
                    # pvdf = pvdf.rename_axis(index_name)
                    # print("Checkpoint#1-3")

                    nn.fit(pvdf)
                  
                    # print("Checkpoint#2")
                    update_array = nn.kneighbors(pivot.iloc[t].values.reshape(1,-1), n_neighbors=N_NEIGHBORS_MAX , return_distance=False)
                                      
                    # print("Checkpoint#3, update_array:", update_array)

                    update_array = update_array.reshape(-1) + (t-window_size)
                    # print("Checkpoint#4")

#                     print("self.neighbors.shape", self.neighbors.shape)
#                     print("update_array.shape", update_array.shape)

                    # self.neighbors = np.append(self.neighbors, update_array, axis = 0)
                    self.neighbors = np.vstack((self.neighbors, update_array))
#                     print("NEWLY UPDATED self.neighbors.shape", self.neighbors.shape)

                    # print("Checkpoint#5")

                    # if t // 10000 == 0 :
                    #    print(t,self.neighbors)
                    gc.collect()


        self.columns = self.index = self.feature_values = self.feature_col = None

    def rearrange_feature_values(self, df: pd.DataFrame, feature_col: str) -> None:
        raise NotImplementedError()

    def make_nn_feature(self, n=5, agg=np.mean) -> pd.DataFrame:
        assert self.feature_values is not None, "should call rearrange_feature_values beforehand"

        start = 1 if self.exclude_self else 0

        pivot_aggs = pd.DataFrame(
            agg(self.feature_values[start:n+start,:,0], axis=0), 
            columns=self.columns, 
            index=self.index[WINDOW_SIZE:]
        )

        dst = pivot_aggs.reset_index() # unstack().
        # print("dst.shape:", dst.shape)
        new_column_names = ['time_id', f'{self.feature_col}_nn{n}_{self.name}_{agg.__name__}'] # 3개를 예측했는데 2개만 들어왔다??
        dst.columns = new_column_names 
        return dst
    

class TimeIdNeighbors(Neighbors):
    def rearrange_feature_values(self, df: pd.DataFrame, feature_col: str, data_df: pd.DataFrame) -> None:
        # feature_pivot = df.pivot(index='time_id', values=feature_col)
        # feature_pivot = feature_pivot.fillna(feature_pivot.mean())

        # print('CHEKCPOINT#1')
        feature_df = data_df[['time_id', feature_col]]
        # print('CHEKCPOINT#2')

        # 첫 WINDOW_SIZE 만큼은 랜덤하게 부여된 이웃이므로 제거.
        # feature_df = feature_df.drop(range(WINDOW_SIZE))

        feature_df.set_index('time_id', inplace=True)
        # feature_df = feature_df.fillna(feature_df.mean())

        feature_values = np.zeros((N_NEIGHBORS_MAX, df.shape[0], 1))
        temp_neighbors = self.neighbors[WINDOW_SIZE:,:]
 
        # print("feature_values", feature_values.shape)
        # print("feature_df", feature_df.shape)
        # print("self.neighbors.shape", self.neighbors.shape)
        # print("temp_neighbors", temp_neighbors.shape)

        for i in range(N_NEIGHBORS_MAX):
            # feature_values[i, :, 0] += feature_df.values[self.neighbors[:, i], 0]
            feature_values[i, :, 0] += feature_df.values[temp_neighbors[:, i], 0]

        self.columns = list(feature_df.columns)
        self.index = list(feature_df.index)
        self.feature_values = feature_values
        self.feature_col = feature_col

    def __repr__(self) -> str:
        return f"time-id NN (name={self.name}, metric={self.metric}, p={self.p})"


### PROGRESS CHECK FUNCTION

In [117]:
@contextmanager
def timer(name: str):
    s = time.time()
    yield
    elapsed = time.time() - s
    print(f'[{name}] {elapsed: .3f}초')

def print_trace(name: str = ''):
    print(f'{name or "익명"}에서 에러가 발생했습니다.')
    print(traceback.format_exc())


### GET NN CLASS. Output: {}_sum_plus_nn_features.csv

In [118]:
from sklearn.preprocessing import StandardScaler
from itertools import combinations

# StandardScaler 객체 생성
scaler = StandardScaler()

USE_ONE_FEATURE_C = False
USE_ONE_FEATURE_M_1 = True
USE_ONE_FEATURE_M_2 = False

USE_TWO_FEATURES = False
USE_TWO_FEATURES_ALL_COMB = False
USE_SEVALRAL_FEATURES = True
USE_ALL_FEATURES = True

USE_HAUSDORFF_FEATURES = True

# Top 5 Related Feature
top_5_high_feat = list(correlation_matrix_series.keys())[1:6]
top_5_low_feat = list(correlation_matrix_series.keys())[-5:]

# Top 5 Absolute Related Feature
sorted_data = correlation_matrix_series.abs().sort_values(ascending=False)
top_5_high_abs_feat = list(sorted_data.head(6).keys())[1:]
top_5_low_abs_feat = list(sorted_data.tail(5).keys())

# time_id_neighbors List 
time_id_neighbors: List[Neighbors] = []

with timer('knn fit'):
    df_pv = combined_result_df_mfl.copy()
    # df_pv = df_pv.drop(['window_start', 'window_end','volume_power'], axis=1)
    
    # Standard All Feature
    # df_pv[feature_list_for_finding_NN] = scaler.fit_transform(df_pv[feature_list_for_finding_NN])

    feature_list = list(df_pv.columns)
    feature_list.remove('time_id') # Can't be standardized
    # feature_list.remove('only_prices_30s_for_NN')
    # feature_list.remove('prices_30s_for_NN_onlyprices') # Can't be standardized
    # feature_list.remove('time_id')
    df_pv[feature_list] = scaler.fit_transform(df_pv[feature_list])
    # combined_result_df_mfl_scaled.head(3)



    #### USE ONLY ONE FACTOR ####

    # ## Canberra Distance
    if USE_ONE_FEATURE_C :
        print("ONE FACTOR: Canberra Distance")
        for feat in feature_list_for_finding_NN :
            gc.collect()
            df_nn = df_pv[['time_id',feat]]
            df_nn.set_index('time_id', inplace=True)
            # df_nn = df_nn.fillna(df_nn.mean())

            time_id_neighbors.append(
                TimeIdNeighbors(
                    feat + '_c', 
                    df_nn, 
                    p=2, 
                    metric='canberra', 
                    exclude_self=True
                )
            )
            
    ## Manhattan Distance
    
    if USE_ONE_FEATURE_M_1:
        print("ONE FACTOR: Manhattan Distance")

        for feat in feature_list_for_finding_NN :
            gc.collect()
            df_nn = df_pv[['time_id',feat]]
            df_nn.set_index('time_id', inplace=True)
            # df_nn = df_nn.fillna(df_nn.mean())

            time_id_neighbors.append(
                TimeIdNeighbors(feat + '_m_p1', df_nn, p=1, exclude_self=True)
            )

    # ## Euclidean Distance
    if USE_ONE_FEATURE_M_2:
        print("ONE FACTOR: Euclidean Distance")

        for feat in feature_list_for_finding_NN :
            gc.collect()
            df_nn = df_pv[['time_id',feat]]
            df_nn.set_index('time_id', inplace=True)
            # df_nn = df_nn.fillna(df_nn.mean())

            time_id_neighbors.append(
                TimeIdNeighbors(feat + '_m_p2', df_nn, p=2, exclude_self=True)
            )


    # #### TWO FACTOR ####

    # if USE_TWO_FEATURES:
    #     feature_list = ['time_id','realized_volatility_mean0','bidask_spread_0'] # target variable이 바뀌면 2번/3번 변수 수정해주어야.
    #     df_nn = df_pv[feature_list]
    #     df_nn.set_index('time_id', inplace=True)
    #     df_nn = df_nn.fillna(df_nn.mean())

    #     ## Canberra

    #     time_id_neighbors.append(
    #             TimeIdNeighbors(
    #                 'two_c',  # before correction: feat + 'two_c', 
    #                 df_nn, 
    #                 p=2, 
    #                 metric='canberra', 
    #                 exclude_self=True
    #             )
    #         )
    #     ## Euclidean Distance
    #     time_id_neighbors.append(
    #         TimeIdNeighbors(
    #             'two_m', 
    #             df_nn, 
    #             p=2, 
    #             exclude_self=True
    #         )
    #     )


    if USE_TWO_FEATURES_ALL_COMB:
        print("TWO FACTORS: all possible combinations")

        combinations_list = list(combinations(feature_list_for_finding_NN, 2))

        for feat in combinations_list :
            gc.collect()
            # feature_list_for_finding_NN
            # combinations_list = list(combinations(feature_list_for_finding_NN, 2))

            feature_list = ['time_id',feat[0],feat[1]] # target variable이 바뀌면 2번/3번 변수 수정해주어야.
            df_nn = df_pv[feature_list]
            df_nn.set_index('time_id', inplace=True)
            # df_nn = df_nn.fillna(df_nn.mean())

            ## Canberra

            # time_id_neighbors.append(
            #         TimeIdNeighbors(
            #             'two_c',  # before correction: feat + 'two_c', 
            #             df_nn, 
            #             p=2, 
            #             metric='canberra', 
            #             exclude_self=True
            #         )
            #     )
            ## Euclidean Distance
            time_id_neighbors.append(
                TimeIdNeighbors(
                    'two_comb_{}_{}_m'.format(feat[0],feat[1]), 
                    df_nn, 
                    p=2, 
                    exclude_self=True
                )
            )



    #### USE SEVALRAL FACTOR ####

    if USE_SEVALRAL_FEATURES:
        print("FIVE FACTORS")

        ## High Related Feature 
        feature_list = ['time_id']
        feature_list += top_5_high_feat
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        # df_nn = df_nn.fillna(df_nn.mean())

        ### Euclidean Distance
        time_id_neighbors.append(
            TimeIdNeighbors(
                'high5_nn_m', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )

        ## Low Related Feature

        feature_list = ['time_id']
        feature_list += top_5_low_feat
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        # df_nn = df_nn.fillna(df_nn.mean())        

        time_id_neighbors.append(
            TimeIdNeighbors(
                'low5_nn_m', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )

        ## High Abs Related Feature

        feature_list = ['time_id']
        feature_list += top_5_high_abs_feat
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        # df_nn = df_nn.fillna(df_nn.mean())
        
        time_id_neighbors.append(
            TimeIdNeighbors(
                'high5_abs_nn_m', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )

        ## Low Abs Related Feature

        feature_list = ['time_id']
        feature_list += top_5_low_abs_feat
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        # df_nn = df_nn.fillna(df_nn.mean())

        time_id_neighbors.append(
            TimeIdNeighbors(
                'low5_abs_nn_m', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )


    #### USE ALL FACTOR ####

    if USE_ALL_FEATURES:
        print("ALL FACTORS")

        df_nn = df_pv.copy()
        # df_nn = df_nn.drop(['dv1_realized_volatility'], axis=1)
        df_nn.set_index('time_id', inplace=True)

        # Standard All Feature
        # df_nn[feature_list_for_finding_NN] = scaler.fit_transform(df_nn[feature_list_for_finding_NN])

        df_nn = df_nn[feature_list_for_finding_NN]
        # df_nn = df_nn.fillna(df_nn.mean())

        time_id_neighbors.append(
            TimeIdNeighbors(
                'all_nn_m_p1', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )

        # time_id_neighbors.append(
        #     TimeIdNeighbors(
        #         'all_nn_m_p2', 
        #         df_nn, 
        #         p=2, 
        #         exclude_self=True
        #     )
        # )

    #### HAUSDORFF

    if USE_HAUSDORFF_FEATURES:
        print("HAUSDORFF")

        time_id_neighbors.append(
                TimeIdNeighbors('hausdorff', None, p=0, exclude_self=True, haus_metric = True)
        )


ONE FACTOR: Manhattan Distance
name: realized_volatility_mean0_m_p1, interation: 0
name: realized_volatility_mean0_m_p1, interation: 1
name: realized_volatility_mean0_m_p1, interation: 2
name: realized_volatility_mean0_m_p1, interation: 3
name: realized_volatility_mean0_m_p1, interation: 4
name: realized_volatility_mean0_m_p1, interation: 5
name: realized_volatility_mean0_m_p1, interation: 6
name: realized_volatility_mean0_m_p1, interation: 7
name: realized_volatility_mean0_m_p1, interation: 8
name: realized_volatility_mean0_m_p1, interation: 9
name: realized_volatility_mean0_m_p1, interation: 10
name: realized_volatility_mean0_m_p1, interation: 11
name: realized_volatility_mean0_m_p1, interation: 12
name: realized_volatility_mean0_m_p1, interation: 13
name: realized_volatility_mean0_m_p1, interation: 14
name: realized_volatility_mean0_m_p1, interation: 15
name: realized_volatility_mean0_m_p1, interation: 16
name: realized_volatility_mean0_m_p1, interation: 17
name: realized_volatility

#### Aggregate Features With NN

In [ ]:
def make_nearest_neighbor_feature(df: pd.DataFrame, data_df: pd.DataFrame) -> pd.DataFrame:
    df2 = df.copy()
    print(df2.shape)

    ### time_id를 기준으로 얻어진 neighbor를 대상으로 feature 만들기
    feature_cols = {
        # 'realized_volatility': [np.mean], #, np.min, np.max, np.std
        'realized_volatility_mean0': [np.mean], # , np.median
        # 'realized_volatility_30s': [np.mean, np.median],

        # 'dv1_realized_volatility': [np.mean],
        'dv2_lowest_return': [np.mean],
        'dv3_highest_return': [np.mean],
        # 'dv4_realized_volatility_30s': [np.mean, np.median],
        'dv5_realized_volatility_mean0': [np.mean],

        'num_trades': [np.mean],
        'lowest_return': [np.mean], # , np.mean, np.min
        'highest_return': [np.mean], # , np.mean, np.min
        'high_low_gap': [np.mean],
        'trade_vol': [np.mean],
        # 'volume_power': [np.mean],
        'BB_width_w10': [np.mean],
        'BB_width_w20': [np.mean],
        'BB_width_w40': [np.mean],

        'liq_last_1': [np.mean],
        'liq_last_2': [np.mean],
        'liq_last_5': [np.mean],
        'ep_liq_1': [np.mean],
        'ep_liq_2': [np.mean],
        'ep_liq_5': [np.mean],
        'bidask_spread_0': [np.mean],
        'bidask_spread_1': [np.mean],

        'tvpl1': [np.mean],
        'tvpl2': [np.mean],
        'tvpl5': [np.mean],
        'tvpl_ep1': [np.mean],
        'tvpl_ep2': [np.mean],
        'tvpl_ep5': [np.mean],
        'trade.tau': [np.mean],
        'return': [np.mean],

    }

    time_id_neigbor_sizes = [2, 4, 8] # 16, 32, 48, 64 메모리 부족으로 계속 오류가 나는 것 같아 이웃 계산 숫자를 줄임.

    ndf: Optional[pd.DataFrame] = None
    
    # 새로운 feature를 기존 df에 추가하는 함수
    def _add_ndf(ndf: Optional[pd.DataFrame], dst: pd.DataFrame) -> pd.DataFrame:
        if ndf is None:
            return dst
        else:
            ndf[dst.columns[-1]] = dst[dst.columns[-1]].astype(np.float32)
            #columns_to_convert = [dst.columns[-1]]  # 열 변환 대상을 선택하거나 여러 열을 지정할 수 있음
            #converted_columns = dst[columns_to_convert].astype(np.float32)
            #ndf = pd.concat([ndf, converted_columns], axis=1)

            return ndf

    # neighbor time_id
    for feature_col in feature_cols.keys():
        gc.collect()
        try: 
            for nn in time_id_neighbors:
                nn.rearrange_feature_values(df2, feature_col, data_df)


            time_id_ns = time_id_neigbor_sizes

            for agg in feature_cols[feature_col]:
                for n in time_id_ns:
                    try:
                        for nn in time_id_neighbors:
                            gc.collect()
                            dst = nn.make_nn_feature(n, agg)
                            ndf = _add_ndf(ndf, dst)
                    except Exception:
                        WHERE_ERROR = feature_col
                        print_trace('time-id nn')
                        pass
        except Exception:
            print_trace('time-id nn')

    if ndf is not None:
        df2 = pd.merge(df2, ndf, on=['time_id'], how='left')
    
    print(df2.shape)
    gc.collect()
    return df2

In [ ]:
# print(type(time_id_neighbors))
print(time_id_neighbors[0].neighbors[:,:10])
print(np.max(time_id_neighbors[0].neighbors[:,:10]))


[[    5     6     2 ...     4     8     3]
 [    9     8     5 ...     1     3     7]
 [    9     1    10 ...     2     8     4]
 ...
 [ 7646  4693  2351 ...  7958 10607  8412]
 [10070  7957  3490 ...  7554  1747  8909]
 [10510  3267  8831 ...  8972  6311  7206]]
11222


In [ ]:
pd.set_option('display.max_columns', None)

combined_result_df.head(3)

realized_volatility_mean0  num_trades  lowest_return  highest_return  \
0                   0.000105         376      -0.000089        0.001815   
1                   0.000107         361      -0.000089        0.001815   
2                   0.000106         365       0.000000        0.001815   

   high_low_gap  trade_vol              time_id  BB_width_w20  BB_width_w40  \
0      0.001904  13.756273  2022-12-16 21:44:00  48144.957031  47257.070312   
1      0.001904  12.615169  2022-12-16 21:45:00  50564.808594  50311.441406   
2      0.001815  13.313910  2022-12-16 21:46:00  53873.535156  53013.300781   

   BB_width_w10  dv5_realized_volatility_mean0  dv2_lowest_return  \
0  55194.203125                       0.000154          -0.000310   
1  54273.382812                       0.000156          -0.000177   
2  51861.355469                       0.000159          -0.000044   

   dv3_highest_return  realized_volatility_mean0_150  num_trades_150  \
0            0.001238                       0.000046              85   
1            0.001371                       0.000077              68   
2            0.001238                       0.000140              69   

   lowest_return_150  highest_return_150  high_low_gap_150  trade_vol_150  \
0          -0.000089            0.000089          0.000177       3.814411   
1          -0.000089            0.000354          0.000443       1.921894   
2           0.000000            0.000354          0.000354       2.159312   

   realized_volatility_mean0_300  num_trades_300  lowest_return_300  \
0                       0.000100             147          -0.000089   
1                       0.000106             126          -0.000089   
2                       0.000109             125           0.000000   

   highest_return_300  high_low_gap_300  trade_vol_300  \
0            0.000354          0.000443       5.543540   
1            0.000399          0.000487       3.760741   
2            0.000753          0.000753       4.498119   

   realized_volatility_mean0_450  num_trades_450  lowest_return_450  \
0                       0.000092             209          -0.000089   
1                       0.000116             259          -0.000089   
2                       0.000119             286           0.000000   

   highest_return_450  high_low_gap_450  trade_vol_450  liq_last_1  \
0            0.001284          0.001373       9.178568    0.003128   
1            0.001815          0.001904       9.098996    0.001286   
2            0.001815          0.001815       9.661851    0.001621   

   liq_last_2  liq_last_5  liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  \
0    0.003207    0.003479     0.003642     0.003871  0.000475  0.000668   
1    0.001625    0.002044     0.002316     0.002420  0.000472  0.000647   
2    0.001628    0.002304     0.002582     0.002729  0.000489  0.000659   

   ep_liq_5  ep_liq_10  ep_liq_15  bidask_spread_0  bidask_spread_1  \
0  0.001029   0.001296   0.001752         2.030769        10.261539   
1  0.000948   0.001205   0.001527         2.098361        13.000000   
2  0.000952   0.001197   0.001454         1.487500         9.412500   

   liq_last_1_150  liq_last_2_150  liq_last_5_150  liq_last_10_150  \
0        0.001555        0.001703        0.002171         0.002716   
1        0.000299        0.000458        0.000700         0.001334   
2        0.000284        0.001064        0.001406         0.001930   

   liq_last_15_150  ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  \
0         0.003101      0.001283      0.001609      0.002627       0.002997   
1         0.001723      0.000869      0.001128      0.001713       0.002192   
2         0.002127      0.000514      0.000769      0.001105       0.001656   

   ep_liq_15_150  bidask_spread_0_150  bidask_spread_1_150  liq_last_1_300  \
0       0.004168             2.000000             9.000000        0.000238   
1       0.002849             5.636364             9.000000        0.001734   
2       

In [ ]:
combined_result_df_mfl.tail(3)

realized_volatility_mean0  num_trades  lowest_return  highest_return  \
11240                   0.000096         245      -0.000047        0.000517   
11241                   0.000100         225       0.000000        0.000517   
11242                   0.000096         246       0.000000        0.000517   

       high_low_gap  trade_vol              time_id  BB_width_w20  \
11240      0.000564   6.481039  2022-12-28 06:24:00  23047.777344   
11241      0.000517   5.446243  2022-12-28 06:25:00  21965.523438   
11242      0.000517   6.187297  2022-12-28 06:26:00  21461.347656   

       BB_width_w40  BB_width_w10  dv5_realized_volatility_mean0  \
11240  21851.714844  19252.705078                       0.000025   
11241  22350.126953  18575.970703                       0.000027   
11242  22789.787109  17833.800781                       0.000027   

       dv2_lowest_return  dv3_highest_return  realized_volatility_mean0_150  \
11240          -0.000141            0.000047                       0.000028   
11241          -0.000235            0.000047                       0.000124   
11242          -0.000329            0.000047                       0.000162   

       num_trades_150  lowest_return_150  highest_return_150  \
11240              60          -0.000047            0.000047   
11241              37           0.000000            0.000517   
11242              42           0.000000            0.000517   

       high_low_gap_150  trade_vol_150  realized_volatility_mean0_300  \
11240          0.000094       1.781470                       0.000110   
11241          0.000517       0.766844                       0.000136   
11242          0.000517       1.105834                       0.000141   

       num_trades_300  lowest_return_300  highest_return_300  \
11240              96          -0.000047            0.000517   
11241              67           0.000000            0.000517   
11242              86           0.000000            0.000517   

       high_low_gap_300  trade_vol_300  realized_volatility_mean0_450  \
11240          0.000564       2.783107                       0.000112   
11241          0.000517       1.532084                       0.000120   
11242          0.000517       2.321465                       0.000115   

       num_trades_450  lowest_return_450  highest_return_450  \
11240             149          -0.000047            0.000517   
11241             151           0.000000            0.000517   
11242             167           0.000000            0.000517   

       high_low_gap_450  trade_vol_450  liq_last_1  liq_last_2  liq_last_5  \
11240          0.000564       4.241177    0.002376    0.003740    0.004152   
11241          0.000517       3.977388    0.005435    0.006746    0.007228   
11242          0.000517       4.221775    0.004195    0.005506    0.005992   

       liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  ep_liq_5  ep_liq_10  \
11240     0.004797     0.006558  0.000839  0.001228  0.001919   0.002953   
11241     0.007810     0.008168  0.000942  0.001405  0.002080   0.003170   
11242     0.006571     0.006825  0.001042  0.001587  0.002243   0.003388   

       ep_liq_15  bidask_spread_0  bidask_spread_1  liq_last_1_150  \
11240   0.004006         1.014706         3.014706        0.001668   
11241   0.004098         1.000000         3.000000        0.000418   
11242   0.004287         1.000000         3.000000        0.000157   

       liq_last_2_150  liq_last_5_150  liq_last_10_150  liq_last_15_150  \
11240        0.001963        0.002400         0.002674         0.002774   
11241        0.001318        0.001478         0.001854         0.004345   
11242        0.000654        0.001644         0.001798         0.003774   

       ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  ep_liq_15_150  \
11240      0.001388      0.001714      0.002221       0.002537       0.003772   
11241      0.000595      0.000859      0.001294       0.001619       0.002701   
11242      0.000455    

In [ ]:
gc.collect()

# Cut the first WINDOW_SIZE rows
# input_df = combined_result_df_mfl.drop(index=range(WINDOW_SIZE))
input_df = combined_result_df_mfl.iloc[WINDOW_SIZE:]

with timer('make nearest neighbor feature'):
    df3 = make_nearest_neighbor_feature(input_df, combined_result_df_mfl)

gc.collect()

(1243, 91)


c:\Users\hhkim\AppData\Local\Programs\Python\Python37\lib\site-packages\ipykernel_launcher.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`


(1243, 2695)
[make nearest neighbor feature]  110.201초


0

In [ ]:
print(df3.shape)
df3.head(3)


(1243, 2695)


realized_volatility_mean0  num_trades  lowest_return  highest_return  \
0                   0.000135         329      -0.000323        0.000415   
1                   0.000127         362      -0.000461        0.000461   
2                   0.000115         395      -0.000692        0.000461   

   high_low_gap  trade_vol              time_id  BB_width_w20  BB_width_w40  \
0      0.000738  10.645347  2022-12-26 20:52:00  18181.541016  28500.832031   
1      0.000923  10.128026  2022-12-26 20:53:00  21169.988281  29650.787109   
2      0.001153  10.053663  2022-12-26 20:54:00  22338.072266  27926.460938   

   BB_width_w10  dv5_realized_volatility_mean0  dv2_lowest_return  \
0  16631.964844                       0.000047          -0.000738   
1  22374.587891                       0.000049          -0.000462   
2  25015.550781                       0.000045          -0.000554   

   dv3_highest_return  realized_volatility_mean0_150  num_trades_150  \
0            0.000000                       0.000161              85   
1            0.000138                       0.000186              78   
2            0.000000                       0.000181              71   

   lowest_return_150  highest_return_150  high_low_gap_150  trade_vol_150  \
0          -0.000231            0.000369          0.000600       3.844748   
1          -0.000185            0.000461          0.000646       3.168875   
2          -0.000185            0.000461          0.000646       2.129523   

   realized_volatility_mean0_300  num_trades_300  lowest_return_300  \
0                       0.000158             139          -0.000231   
1                       0.000155             142          -0.000185   
2                       0.000139             146          -0.000185   

   highest_return_300  high_low_gap_300  trade_vol_300  \
0            0.000415          0.000646       4.919937   
1            0.000461          0.000646       4.610876   
2            0.000461          0.000646       4.074956   

   realized_volatility_mean0_450  num_trades_450  lowest_return_450  \
0                       0.000140             216          -0.000231   
1                       0.000156             211          -0.000185   
2                       0.000141             246          -0.000277   

   highest_return_450  high_low_gap_450  trade_vol_450  liq_last_1  \
0            0.000415          0.000646       7.069295    0.000369   
1            0.000461          0.000646       6.356064    0.000325   
2            0.000461          0.000738       7.407062    0.000089   

   liq_last_2  liq_last_5  liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  \
0    0.000458    0.000848     0.001282     0.001617  0.000223  0.000398   
1    0.000598    0.000857     0.001416     0.001805  0.000235  0.000416   
2    0.000334    0.000624     0.001067     0.001451  0.000259  0.000437   

   ep_liq_5  ep_liq_10  ep_liq_15  bidask_spread_0  bidask_spread_1  \
0  0.001022   0.001262   0.001566         1.317647         6.035294   
1  0.001033   0.001334   0.001642         1.585366         4.439024   
2  0.001000   0.001342   0.001665         2.552083         7.562500   

   liq_last_1_150  liq_last_2_150  liq_last_5_150  liq_last_10_150  \
0        0.000111        0.003431        0.003471         0.003809   
1        0.000376        0.000417        0.001453         0.001653   
2        0.000475        0.000745        0.002558         0.002766   

   liq_last_15_150  ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  \
0         0.004056      0.000118      0.000282      0.000624       0.000804   
1         0.002057      0.000132      0.000340      0.000793       0.000983   
2         0.003102      0.000171      0.000404      0.001003       0.001187   

   ep_liq_15_150  bidask_spread_0_150  bidask_spread_1_150  liq_last_1_300  \
0       0.001050             7.428571            11.857142        0.000328   
1       0.001254             8.235294            10.441176        0.000214   
2       

In [52]:
# df3.to_csv(working_directory + "output\\temp_1027_1.csv", index=False)

In [ ]:
# Cut the first 'window_size' (15,000 or something) rows. <= These rows do not have appropriate nearest neighbors.
# WINDOW_SIZE=20000
# df3 = df3.drop(index=range(WINDOW_SIZE))

coin = 'BTC'
df3.to_csv(working_directory + "output\\{}_sum_plus_nn_features_for_{}.csv".format(coin, target_var_3), index=False)

## NN 추출끼리 비슷한가 아니면 다른가?

In [ ]:
def calculate_rank_correraltion(neighbors, top_n=10):
    if not neighbors:
        return
    neighbor_indices = pd.DataFrame()
    for n in neighbors:
        neighbor_indices[n.name] = n.neighbors[:,:top_n].flatten()
        display(neighbor_indices[n.name])
    sns.heatmap(neighbor_indices.corr('kendall'), annot=True)
    

In [ ]:
time_ids = np.array(sorted(df3['time_id'].unique()))
for neighbor in time_id_neighbors:
    print(neighbor)
    display(
        pd.DataFrame(
            time_ids[neighbor.neighbors[:,:10]], 
            index=pd.Index(time_ids, name='time_id'), 
            columns=[f'top_{i+1}' for i in range(10)]
        ).iloc[1:6]
    )
    print(pd.DataFrame(
            time_ids[neighbor.neighbors[:,:10]], 
            index=pd.Index(time_ids, name='time_id'), 
            columns=[f'top_{i+1}' for i in range(10)]
        ).shape)

In [ ]:
calculate_rank_correraltion(time_id_neighbors)

In [ ]:
# # TEMP code

# import gc
# import pandas as pd
# import os
# os.environ["MODIN_ENGINE"] = "dask"  # Modin will use Dask
# working_directory = 'D:\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'  ## 서로 다른 환경에서는 이곳을 수정해야 함.
# # working_directory = 'C:\\Users\\user\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'

# os.chdir(working_directory)
# gc.collect()

# # combined_result_df = pd.read_csv("./DB/professor_BTC_sum_both_10m.csv")
# coin = 'BTC'
# target_var = 'dv5_realized_volatility_mean0'
# target_var_3 = target_var[:3]
# df3 = pd.read_csv("./output/{}_sum_plus_nn_features_for_{}.csv".format(coin, target_var_3))

# window_size=10000
# df3 = df3.drop(index=range(window_size))
# df3.to_csv(working_directory + "output\\{}_sum_plus_nn_features_for_{}.csv".format(coin, target_var_3), index=False)


### Checking the final outcome

In [ ]:
import gc
import pandas as pd
import os
os.environ["MODIN_ENGINE"] = "dask"  # Modin will use Dask
working_directory = 'D:\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'  ## 서로 다른 환경에서는 이곳을 수정해야 함.
# working_directory = 'C:\\Users\\user\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'

os.chdir(working_directory)
gc.collect()

# combined_result_df = pd.read_csv("./DB/professor_BTC_sum_both_10m.csv")
coin = 'BTC'
target_var = 'dv5_realized_volatility_mean0'
target_var_3 = target_var[:3]
df3 = pd.read_csv("./output/{}_sum_plus_nn_features_for_{}.csv".format(coin, target_var_3))

df3.head(3)
print("# of rows:", df3.shape[0])
print("# of columns:", df3.shape[1])

In [ ]:
df3.columns